# Демонстрация автоматического расчета важностей

In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container {width:95% !important;}</style>"))

import warnings
warnings.filterwarnings('ignore')

In [2]:
# Стандартные библиотеки для анализа
import pandas as pd
pd.options.display.float_format = '{:20,.2f}'.format

import numpy as np
from sklearn.model_selection import train_test_split, KFold
import matplotlib.pylab as pl

from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor

from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from lightgbm import LGBMRegressor

In [3]:
import sys
sys.path.append('../')

# Наша разработанная библиотека
from autobinary import SentColumns, CatBoostEncoder, AutoTrees, base_pipe

In [4]:
import sklearn as sk
import xgboost as xgb
import matplotlib as mplot
import autobinary as ab

print('sklearn: ', sk.__version__)
print('xgboost: ', xgb.__version__)
print('matplotlib: ', mplot.__version__)
print('autobinary: ', ab.__version__)

sklearn:  1.2.1
xgboost:  1.5.2
matplotlib:  3.7.0
autobinary:  1.0.9


## 1.1 Загрузка выборки

In [5]:
sample = pd.read_csv('../data/train_houseprice.csv')

print('Размерность данных:', sample.shape)
sample.head(2)

Размерность данных: (1460, 81)


Id  MSSubClass MSZoning          LotFrontage  LotArea Street Alley  \
0   1          60       RL                65.00     8450   Pave   NaN   
1   2          20       RL                80.00     9600   Pave   NaN   

  LotShape LandContour Utilities  ... PoolArea PoolQC Fence MiscFeature  \
0      Reg         Lvl    AllPub  ...        0    NaN   NaN         NaN   
1      Reg         Lvl    AllPub  ...        0    NaN   NaN         NaN   

  MiscVal MoSold YrSold  SaleType  SaleCondition  SalePrice  
0       0      2   2008        WD         Normal     208500  
1       0      5   2007        WD         Normal     181500  

[2 rows x 81 columns]

In [6]:
num_columns = [
    'LotArea', 'LotFrontage', 'TotalBsmtSF', 'PoolArea', 'FullBath'
]

cat_columns = [
    'BldgType', 'CentralAir', 'GarageQual', 'Fence', 'SaleType'
]

target = ['SalePrice']

In [7]:
X_train, X_val, y_train, y_val = train_test_split(
    sample[num_columns+cat_columns],
    sample[target],
    test_size=0.3,
    random_state=42
)

In [8]:
y_train[target].mean()

SalePrice             181,312.69
dtype: float64

In [9]:
y_val[target].mean()

SalePrice             180,007.70
dtype: float64

## 1.2 Определяем конвейер обработки, стратегию CV

In [10]:
prep_pipe = base_pipe(
    num_columns=num_columns, 
    cat_columns=cat_columns)

Определены количественные и категориальные переменные!


In [11]:
# задаем стратегию проверки
strat = KFold(
    n_splits=3,
    shuffle=True,
    random_state=42)

## 2. DecisionTreeRegressor

In [12]:
params = {
    'criterion':'squared_error',
    'max_depth':5,
    'random_state':42}

fit_params = {}

dt = DecisionTreeRegressor(**params)

In [13]:
dt_model = AutoTrees(
    main_estimator=dt, 
    main_fit_params=fit_params,
    main_prep_pipe = prep_pipe,
    main_features=num_columns+cat_columns,
    
    X_train=X_train,
    y_train=y_train,
    
    main_metric='rmse',
    model_type = 'decisiontree')

In [14]:
dt_model.model_fit_cv(strat=strat)

1it [00:00,  9.61it/s]

==================== Обучение 1 фолда! ====================
rmse на обучающей выборке: 42627.775
rmse на проверочной выборке: 69226.440

********************** 1 фолд обучен! ******************************


==================== Обучение 2 фолда! ====================


3it [00:00,  6.76it/s]

rmse на обучающей выборке: 39851.574
rmse на проверочной выборке: 64432.509

********************** 2 фолд обучен! ******************************


==================== Обучение 3 фолда! ====================
rmse на обучающей выборке: 37576.294
rmse на проверочной выборке: 60019.203

********************** 3 фолд обучен! ******************************




In [15]:
dt_model.get_mean_cv_scores()

64559.38413951845

In [16]:
dt_model.get_extra_scores()

names               fold_1               fold_2               fold_3
0   mae_train            29,930.57            28,532.63            26,731.56
1   mae_valid            41,030.85            39,286.95            36,494.40
2   mse_train     1,817,127,228.04     1,588,147,989.12     1,411,977,870.82
3   mse_valid     4,792,300,026.04     4,151,548,208.58     3,602,304,759.09
4  rmse_train            42,627.78            39,851.57            37,576.29
5  rmse_valid            69,226.44            64,432.51            60,019.20

In [17]:
fi = dt_model.get_fi()
fi

index         importance 0         importance 1         importance 2  \
0  TotalBsmtSF                 0.57                 0.58                 0.50   
1     FullBath                 0.16                 0.19                 0.28   
2  LotFrontage                 0.05                 0.08                 0.06   
3     BldgType                 0.05                 0.03                 0.08   
4      LotArea                 0.03                 0.06                 0.05   
5     SaleType                 0.03                 0.03                 0.00   
6   GarageQual                 0.03                 0.03                 0.00   
7        Fence                 0.05                 0.00                 0.00   
8   CentralAir                 0.02                 0.01                 0.02   
9     PoolArea                 0.00                 0.00                 0.00   

       mean_importance  
0                 0.55  
1                 0.21  
2                 0.06  
3                 0.05  
4                 0.05  
5                 0.02  
6                 0.02  
7                 0.02  
8                 0.02  
9                 0.00

## 3. RandomForestRegressor

In [18]:
params = {
    'criterion':'squared_error',
    'max_depth':5,
    'random_state':42,
    'n_estimators':50}

fit_params = {}

rf = RandomForestRegressor(**params)

In [19]:
rf_model = AutoTrees(
    main_estimator=rf, 
    main_fit_params=fit_params,
    main_prep_pipe = prep_pipe,
    main_features=num_columns+cat_columns,
    
    X_train=X_train,
    y_train=y_train,
    
    main_metric='rmse',
    model_type = 'randomforest')

In [20]:
rf_model.model_fit_cv(strat=strat)

0it [00:00, ?it/s]

==================== Обучение 1 фолда! ====================


1it [00:00,  5.16it/s]

rmse на обучающей выборке: 37981.756
rmse на проверочной выборке: 46810.880

********************** 1 фолд обучен! ******************************


==================== Обучение 2 фолда! ====================


2it [00:00,  5.43it/s]

rmse на обучающей выборке: 37823.338
rmse на проверочной выборке: 50472.571

********************** 2 фолд обучен! ******************************


==================== Обучение 3 фолда! ====================


3it [00:00,  5.49it/s]

rmse на обучающей выборке: 35459.508
rmse на проверочной выборке: 54287.541

********************** 3 фолд обучен! ******************************




In [21]:
rf_model.get_mean_cv_scores()

50523.66414689851

In [22]:
rf_model.get_extra_scores()

names               fold_1               fold_2               fold_3
0   mae_train            27,174.23            27,122.08            25,815.23
1   mae_valid            33,118.50            32,469.29            33,403.54
2   mse_train     1,442,613,774.56     1,430,604,878.95     1,257,376,695.41
3   mse_valid     2,191,258,474.28     2,547,480,433.53     2,947,137,158.75
4  rmse_train            37,981.76            37,823.34            35,459.51
5  rmse_valid            46,810.88            50,472.57            54,287.54

In [23]:
fi = rf_model.get_fi()
fi

index         importance 0         importance 1         importance 2  \
0  TotalBsmtSF                 0.57                 0.53                 0.42   
1     FullBath                 0.19                 0.23                 0.35   
2      LotArea                 0.07                 0.08                 0.10   
3  LotFrontage                 0.05                 0.05                 0.04   
4     BldgType                 0.04                 0.03                 0.05   
5     SaleType                 0.02                 0.02                 0.01   
6   CentralAir                 0.02                 0.02                 0.02   
7     PoolArea                 0.03                 0.02                 0.00   
8   GarageQual                 0.02                 0.02                 0.01   
9        Fence                 0.00                 0.00                 0.00   

       mean_importance  
0                 0.50  
1                 0.26  
2                 0.08  
3                 0.04  
4                 0.04  
5                 0.02  
6                 0.02  
7                 0.02  
8                 0.02  
9                 0.00

## 4. XGBRegressor

In [24]:
params = {
    'eta':0.01,
    'n_estimators':1000,
    'subsample':0.9,
    'colsample_bytree':0.6,
    'max_depth':6,
    'objective':'reg:squarederror',
    'n_jobs':-1,
    'random_state':42}

fit_params = {
    'early_stopping_rounds':200, 
    'eval_metric':'rmse',
    'verbose':50}

xgb = XGBRegressor(**params)

In [25]:
xgb_model = AutoTrees(
    main_estimator=xgb, 
    main_fit_params=fit_params,
    main_prep_pipe = prep_pipe,
    main_features=num_columns+cat_columns,
    
    X_train=X_train,
    y_train=y_train,
    
    main_metric='mape',
    model_type = 'xgboost')

In [26]:
xgb_model.model_fit_cv(strat=strat)

0it [00:00, ?it/s]

==================== Обучение 1 фолда! ====================
[0]	validation_0-rmse:198388.87500	validation_1-rmse:189377.35938
[50]	validation_0-rmse:127582.07812	validation_1-rmse:121080.61719
[100]	validation_0-rmse:85580.90625	validation_1-rmse:81691.11719
[150]	validation_0-rmse:60365.14453	validation_1-rmse:60295.39062
[200]	validation_0-rmse:45620.53906	validation_1-rmse:49884.48047
[250]	validation_0-rmse:36938.44922	validation_1-rmse:45401.64844
[300]	validation_0-rmse:32013.08594	validation_1-rmse:43663.23438
[350]	validation_0-rmse:29039.93555	validation_1-rmse:43077.52734
[400]	validation_0-rmse:27063.90625	validation_1-rmse:42936.77344
[450]	validation_0-rmse:25602.40430	validation_1-rmse:42922.38672
[500]	validation_0-rmse:24425.60156	validation_1-rmse:42914.98438
[550]	validation_0-rmse:23607.84570	validation_1-rmse:42991.66016
[600]	validation_0-rmse:22862.62305	validation_1-rmse:43104.96094
[633]	validation_0-rmse:22334.65234	validation_1-rmse:43110.57422


1it [00:00,  1.30it/s]

BEST ITERATION:  434
mape на обучающей выборке: 0.101
mape на проверочной выборке: 0.185

********************** 1 фолд обучен! ******************************


==================== Обучение 2 фолда! ====================
[0]	validation_0-rmse:199086.67188	validation_1-rmse:187837.50000
[50]	validation_0-rmse:127943.14844	validation_1-rmse:119597.99219
[100]	validation_0-rmse:85926.85938	validation_1-rmse:81188.29688
[150]	validation_0-rmse:61082.99219	validation_1-rmse:60716.01562
[200]	validation_0-rmse:46793.99219	validation_1-rmse:50552.10156
[250]	validation_0-rmse:38521.19141	validation_1-rmse:46034.32422
[300]	validation_0-rmse:33786.35938	validation_1-rmse:44133.85156
[350]	validation_0-rmse:30703.49023	validation_1-rmse:43217.26953
[400]	validation_0-rmse:28673.79883	validation_1-rmse:42842.87500
[450]	validation_0-rmse:27143.68555	validation_1-rmse:42645.43750
[500]	validation_0-rmse:26032.01562	validation_1-rmse:42531.96875
[550]	validation_0-rmse:25134.87305	validation_1-rms

2it [00:01,  1.14it/s]

BEST ITERATION:  630
mape на обучающей выборке: 0.102
mape на проверочной выборке: 0.168

********************** 2 фолд обучен! ******************************


==================== Обучение 3 фолда! ====================
[0]	validation_0-rmse:188640.20312	validation_1-rmse:208469.35938
[50]	validation_0-rmse:120941.39062	validation_1-rmse:140212.59375
[100]	validation_0-rmse:80450.67969	validation_1-rmse:100426.11719
[150]	validation_0-rmse:56600.60156	validation_1-rmse:78915.03906
[200]	validation_0-rmse:42598.74609	validation_1-rmse:67550.75781
[250]	validation_0-rmse:34758.57422	validation_1-rmse:61828.59375
[300]	validation_0-rmse:30054.37695	validation_1-rmse:58687.78906
[350]	validation_0-rmse:27367.99023	validation_1-rmse:57274.70312
[400]	validation_0-rmse:25603.57422	validation_1-rmse:56502.05078
[450]	validation_0-rmse:24321.00781	validation_1-rmse:56205.58984
[500]	validation_0-rmse:23338.26562	validation_1-rmse:56103.89844
[550]	validation_0-rmse:22542.18359	validation_1-rm

3it [00:02,  1.17it/s]

mape на обучающей выборке: 0.101
mape на проверочной выборке: 0.167

********************** 3 фолд обучен! ******************************




In [27]:
xgb_model.get_mean_cv_scores()

0.17366091296114003

In [28]:
xgb_model._best_iters

[434, 630, 540]

In [29]:
xgb_model.get_extra_scores()

names               fold_1               fold_2               fold_3
0   mae_train            18,503.73            17,294.96            16,642.67
1   mae_valid            30,728.38            29,055.78            33,309.26
2   mse_train       679,586,124.89       566,544,198.85       514,039,100.18
3   mse_valid     1,840,259,554.49     1,802,816,970.68     3,137,965,259.51
4  rmse_train            26,068.87            23,802.19            22,672.43
5  rmse_valid            42,898.25            42,459.59            56,017.54

In [30]:
fi = xgb_model.get_fi()
fi

index         importance 0         importance 1         importance 2  \
0     FullBath    34,952,355,840.00    33,296,699,392.00    33,161,064,448.00   
1  TotalBsmtSF    16,201,422,848.00    12,633,034,752.00     7,502,221,312.00   
2     SaleType     8,990,325,760.00     9,131,326,464.00     5,181,465,600.00   
3   CentralAir     9,841,988,608.00     5,597,278,720.00     6,236,506,112.00   
4     BldgType     8,139,835,904.00     5,784,364,544.00     6,416,704,000.00   
5     PoolArea     7,316,493,312.00     9,313,934,336.00     1,331,123,840.00   
6   GarageQual     4,730,639,360.00     4,423,862,272.00     4,385,095,680.00   
7      LotArea     5,089,410,048.00     3,860,668,928.00     3,282,997,248.00   
8  LotFrontage     3,570,960,640.00     2,485,466,880.00     2,005,310,080.00   
9        Fence     2,354,578,688.00     2,187,159,040.00     2,093,010,304.00   

       mean_importance  
0    33,803,373,226.67  
1    12,112,226,304.00  
2     7,767,705,941.33  
3     7,225,257,813.33  
4     6,780,301,482.67  
5     5,987,183,829.33  
6     4,513,199,104.00  
7     4,077,692,074.67  
8     2,687,245,866.67  
9     2,211,582,677.33

In [31]:
xgb_model.get_curve_plots()

## 5. LGBMRegressor

In [32]:
params = {
    'learning_rate':0.01,
    'n_estimators':1000,
    'subsample':0.9,
    'colsample_bytree':0.6,
    'max_depth':6,
    'objective':'regression',
    'n_jobs':-1,
    'random_state':42}

fit_params = {
    'early_stopping_rounds':200, 
    'eval_metric':'rmse',
    'verbose':50}

# создаем экземпляр класса XGBClassifier
lgb = LGBMRegressor(**params)

In [33]:
lgb_model = AutoTrees(
    main_estimator=lgb, 
    main_fit_params=fit_params,
    main_prep_pipe = prep_pipe,
    main_features=num_columns+cat_columns,
    
    X_train=X_train,
    y_train=y_train,
    main_metric='mape',
    model_type = 'lightboost')

In [34]:
lgb_model.model_fit_cv(strat=strat)

0it [00:00, ?it/s]

==================== Обучение 1 фолда! ====================
[50]	training's rmse: 64461	training's l2: 4.15521e+09	valid_1's rmse: 58935.3	valid_1's l2: 3.47336e+09
[100]	training's rmse: 54900.5	training's l2: 3.01407e+09	valid_1's rmse: 52204.3	valid_1's l2: 2.72529e+09


1it [00:00,  1.40it/s]

[150]	training's rmse: 49529.1	training's l2: 2.45314e+09	valid_1's rmse: 48919.9	valid_1's l2: 2.39316e+09
[200]	training's rmse: 46292.3	training's l2: 2.14298e+09	valid_1's rmse: 47285.6	valid_1's l2: 2.23593e+09
[250]	training's rmse: 44466	training's l2: 1.97723e+09	valid_1's rmse: 46380.2	valid_1's l2: 2.15112e+09
[300]	training's rmse: 43264.7	training's l2: 1.87183e+09	valid_1's rmse: 45817.1	valid_1's l2: 2.09921e+09
[350]	training's rmse: 42368.8	training's l2: 1.79511e+09	valid_1's rmse: 45438.9	valid_1's l2: 2.06469e+09
[400]	training's rmse: 41641.3	training's l2: 1.734e+09	valid_1's rmse: 45115.5	valid_1's l2: 2.03541e+09
[450]	training's rmse: 41117.5	training's l2: 1.69065e+09	valid_1's rmse: 44918.4	valid_1's l2: 2.01766e+09
[500]	training's rmse: 40709.3	training's l2: 1.65725e+09	valid_1's rmse: 44819.4	valid_1's l2: 2.00877e+09
[550]	training's rmse: 40296	training's l2: 1.62376e+09	valid_1's rmse: 44877.6	valid_1's l2: 2.014e+09
[600]	training's rmse: 39936	trainin

2it [00:01,  1.92it/s]

[700]	training's rmse: 37768.6	training's l2: 1.42646e+09	valid_1's rmse: 46729.5	valid_1's l2: 2.18365e+09
[750]	training's rmse: 37292.5	training's l2: 1.39073e+09	valid_1's rmse: 46739.5	valid_1's l2: 2.18458e+09
BEST ITERATION:  557
mape на обучающей выборке: 0.148
mape на проверочной выборке: 0.178

********************** 2 фолд обучен! ******************************


==================== Обучение 3 фолда! ====================
[50]	training's rmse: 58218.6	training's l2: 3.38941e+09	valid_1's rmse: 74758.6	valid_1's l2: 5.58885e+09
[100]	training's rmse: 50260.6	training's l2: 2.52613e+09	valid_1's rmse: 65935.4	valid_1's l2: 4.34747e+09
[150]	training's rmse: 45519.3	training's l2: 2.07201e+09	valid_1's rmse: 60725.8	valid_1's l2: 3.68762e+09
[200]	training's rmse: 42630	training's l2: 1.81732e+09	valid_1's rmse: 57558.2	valid_1's l2: 3.31295e+09
[250]	training's rmse: 40768	training's l2: 1.66203e+09	valid_1's rmse: 55776	valid_1's l2: 3.11096e+09
[300]	training's rmse: 39468	t

3it [00:01,  2.03it/s]

mape на обучающей выборке: 0.146
mape на проверочной выборке: 0.170

********************** 3 фолд обучен! ******************************




In [35]:
lgb_model.get_mean_cv_scores()

0.18063233452718205

In [36]:
lgb_model._best_iters

[507, 557, 505]

In [37]:
lgb_model.get_extra_scores()

names               fold_1               fold_2               fold_3
0   mae_train            25,744.32            25,888.33            24,816.22
1   mae_valid            31,372.81            30,403.26            33,223.33
2   mse_train     1,653,879,424.26     1,530,407,618.22     1,363,617,564.10
3   mse_valid     2,007,331,202.71     2,178,051,357.94     2,817,273,193.41
4  rmse_train            40,667.92            39,120.42            36,927.19
5  rmse_valid            44,803.25            46,669.60            53,077.99

In [38]:
fi = lgb_model.get_fi()
fi

index          importance 0          importance 1  \
0  TotalBsmtSF 78,536,609,609,293.00 72,730,151,492,104.00   
1     FullBath 29,381,155,954,560.00 35,911,452,600,288.00   
2      LotArea 23,715,256,227,362.00 24,768,265,349,554.00   
3  LotFrontage 13,953,753,184,066.50 13,518,057,808,216.00   
4     SaleType  6,860,829,247,070.00  8,803,850,589,592.00   
5     BldgType  5,832,470,583,730.00  4,958,343,227,800.00   
6   CentralAir  3,586,467,190,673.31  2,634,604,007,456.00   
7   GarageQual  2,334,638,857,720.00  2,466,338,623,356.00   
8        Fence  1,229,052,406,088.00  2,167,860,437,628.00   
9     PoolArea                  0.00                  0.00   

           importance 2       mean_importance  
0 47,749,443,599,554.24 66,338,734,900,317.09  
1 28,178,495,178,496.00 31,157,034,577,781.33  
2 23,048,396,383,026.00 23,843,972,653,314.00  
3  9,526,502,306,965.40 12,332,771,099,749.30  
4  4,865,109,552,336.00  6,843,263,129,666.00  
5  6,272,462,044,626.00  5,687,758,618,718.67  
6  3,309,601,383,896.00  3,176,890,860,675.10  
7  2,885,250,675,018.00  2,562,076,052,031.33  
8  2,054,426,896,095.00  1,817,113,246,603.67  
9                  0.00                  0.00

In [39]:
lgb_model.get_curve_plots()

## 6. CatBoostRegressor - MAPE

In [40]:
params = {
    'learning_rate':0.01,
    'iterations':1000,
    'subsample':0.9,
    'colsample_bylevel':0.9,
    'depth':6,
    'loss_function':'MAPE',
    'thread_count':-1,
    'random_state':42,
    'eval_metric':'MAPE',
    'custom_metric':'MAE',
    'logging_level':'Verbose'}

fit_params = {
    'use_best_model':True,
    'early_stopping_rounds':200, 
    'verbose':50,
    'plot':False}

# создаем экземпляр класса XGBClassifier
catb = CatBoostRegressor(**params)

In [41]:
catb_model_1 = AutoTrees(
    main_estimator=catb, 
    main_fit_params=fit_params,
    main_prep_pipe = prep_pipe,
    main_features=num_columns+cat_columns,
    
    X_train=X_train,
    y_train=y_train,
    main_metric='mape',
    model_type = 'catboost')

In [42]:
catb_model_1.model_fit_cv(strat=strat)

0it [00:00, ?it/s]

==================== Обучение 1 фолда! ====================
0:	learn: 0.2916038	test: 0.2916038	test1: 0.2949008	best: 0.2949008 (0)	total: 52.1ms	remaining: 52.1s
50:	learn: 0.2734544	test: 0.2734544	test1: 0.2821159	best: 0.2821159 (50)	total: 93.1ms	remaining: 1.73s
100:	learn: 0.2637368	test: 0.2637368	test1: 0.2755607	best: 0.2755607 (100)	total: 126ms	remaining: 1.13s
150:	learn: 0.2550280	test: 0.2550280	test1: 0.2688672	best: 0.2688672 (150)	total: 156ms	remaining: 875ms
200:	learn: 0.2482925	test: 0.2482925	test1: 0.2644480	best: 0.2644480 (200)	total: 182ms	remaining: 722ms
250:	learn: 0.2424390	test: 0.2424390	test1: 0.2605604	best: 0.2605604 (250)	total: 208ms	remaining: 621ms
300:	learn: 0.2387001	test: 0.2387001	test1: 0.2584970	best: 0.2584970 (300)	total: 236ms	remaining: 547ms
350:	learn: 0.2356392	test: 0.2356392	test1: 0.2564463	best: 0.2564463 (350)	total: 264ms	remaining: 487ms
400:	learn: 0.2325070	test: 0.2325070	test1: 0.2543495	best: 0.2543495 (400)	total: 291m

1it [00:00,  1.15it/s]

750:	learn: 0.2195574	test: 0.2195574	test1: 0.2476560	best: 0.2476526 (748)	total: 513ms	remaining: 170ms
800:	learn: 0.2184984	test: 0.2184984	test1: 0.2473160	best: 0.2473160 (800)	total: 541ms	remaining: 134ms
850:	learn: 0.2175713	test: 0.2175713	test1: 0.2469639	best: 0.2469580 (843)	total: 571ms	remaining: 99.9ms
900:	learn: 0.2169951	test: 0.2169951	test1: 0.2468066	best: 0.2468041 (898)	total: 601ms	remaining: 66ms
950:	learn: 0.2164361	test: 0.2164361	test1: 0.2465599	best: 0.2465565 (949)	total: 629ms	remaining: 32.4ms
999:	learn: 0.2160873	test: 0.2160873	test1: 0.2464729	best: 0.2464724 (998)	total: 658ms	remaining: 0us

bestTest = 0.2464723603
bestIteration = 998

Shrink model to first 999 iterations.
BEST ITERATION:  998
mape на обучающей выборке: 0.216
mape на проверочной выборке: 0.246

********************** 1 фолд обучен! ******************************


==================== Обучение 2 фолда! ====================
0:	learn: 0.3017868	test: 0.3017868	test1: 0.2741534	b

2it [00:01,  1.21it/s]

999:	learn: 0.2151240	test: 0.2151240	test1: 0.2168045	best: 0.2168034 (998)	total: 596ms	remaining: 0us

bestTest = 0.2168034304
bestIteration = 998

Shrink model to first 999 iterations.
BEST ITERATION:  998
mape на обучающей выборке: 0.215
mape на проверочной выборке: 0.217

********************** 2 фолд обучен! ******************************


==================== Обучение 3 фолда! ====================
0:	learn: 0.2846038	test: 0.2846038	test1: 0.3093511	best: 0.3093511 (0)	total: 714us	remaining: 714ms
50:	learn: 0.2673401	test: 0.2673401	test1: 0.2930225	best: 0.2930225 (50)	total: 34.2ms	remaining: 637ms
100:	learn: 0.2560047	test: 0.2560047	test1: 0.2830181	best: 0.2830181 (100)	total: 67.8ms	remaining: 603ms
150:	learn: 0.2489051	test: 0.2489051	test1: 0.2773232	best: 0.2773232 (150)	total: 100ms	remaining: 565ms
200:	learn: 0.2422405	test: 0.2422405	test1: 0.2721824	best: 0.2721824 (200)	total: 134ms	remaining: 533ms
250:	learn: 0.2364905	test: 0.2364905	test1: 0.2678176	best

3it [00:02,  1.19it/s]

mape на обучающей выборке: 0.209
mape на проверочной выборке: 0.255

********************** 3 фолд обучен! ******************************




In [43]:
catb_model_1.get_mean_cv_scores()

0.23947945744371227

In [44]:
catb_model_1._best_iters

[998, 998, 995]

In [45]:
catb_model_1.get_extra_scores()

names               fold_1               fold_2               fold_3
0   mae_train            47,741.53            46,374.29            43,116.18
1   mae_valid            47,773.93            42,552.28            58,156.73
2   mse_train     6,001,063,557.12     5,515,236,633.15     4,730,750,676.17
3   mse_valid     4,983,948,177.98     4,574,666,145.89     8,490,959,598.63
4  rmse_train            77,466.53            74,264.64            68,780.45
5  rmse_valid            70,597.08            67,636.28            92,146.40

In [46]:
fi = catb_model_1.get_fi()
fi

index         importance_0         importance_1         importance_2  \
0     FullBath                19.64                16.91                27.21   
1  TotalBsmtSF                13.49                19.78                18.95   
2      LotArea                12.15                18.04                15.91   
3     PoolArea                17.95                 9.60                 1.92   
4   GarageQual                 9.35                 7.73                 7.65   
5   CentralAir                 6.20                 6.01                 9.25   
6  LotFrontage                 6.48                 7.86                 6.54   
7     SaleType                 7.35                 6.91                 4.73   
8     BldgType                 3.50                 4.21                 5.51   
9        Fence                 3.91                 2.94                 2.33   

       mean_importance  
0                21.25  
1                17.41  
2                15.37  
3                 9.82  
4                 8.24  
5                 7.15  
6                 6.96  
7                 6.33  
8                 4.40  
9                 3.06

In [47]:
catb_model_1.get_curve_plots()

## 7. CatBoostRegressor - SMAPE

In [48]:
params = {
    'learning_rate':0.01,
    'iterations':2000,
    'subsample':0.9,
    'colsample_bylevel':0.9,
    'depth':6,
    'loss_function':'MAPE',
    'thread_count':-1,
    'random_state':42,
    'eval_metric':'SMAPE',
    'custom_metric':'MAPE',
    'logging_level':'Verbose'}

fit_params = {
    'use_best_model':True,
    'early_stopping_rounds':200, 
    'verbose':50,
    'plot':False}

# создаем экземпляр класса XGBClassifier
catb = CatBoostRegressor(**params)

In [49]:
catb_model_2 = AutoTrees(
    main_estimator=catb, 
    main_fit_params=fit_params,
    main_prep_pipe = prep_pipe,
    main_features=num_columns+cat_columns,
    
    X_train=X_train,
    y_train=y_train,
    
    main_metric='mape',
    model_type = 'catboost')

In [50]:
catb_model_2.model_fit_cv(strat=strat)

0it [00:00, ?it/s]

==================== Обучение 1 фолда! ====================
0:	learn: 31.6931125	test: 31.6931125	test1: 31.2687152	best: 31.2687152 (0)	total: 754us	remaining: 1.51s
50:	learn: 29.9725116	test: 29.9725116	test1: 29.9710641	best: 29.9710641 (50)	total: 32.7ms	remaining: 1.25s
100:	learn: 29.0767090	test: 29.0767090	test1: 29.3343832	best: 29.3343832 (100)	total: 61ms	remaining: 1.15s
150:	learn: 28.2312534	test: 28.2312534	test1: 28.6607746	best: 28.6607746 (150)	total: 92.6ms	remaining: 1.13s
200:	learn: 27.5020794	test: 27.5020794	test1: 28.1607294	best: 28.1607294 (200)	total: 124ms	remaining: 1.11s
250:	learn: 26.9606752	test: 26.9606752	test1: 27.7874902	best: 27.7874902 (250)	total: 155ms	remaining: 1.08s
300:	learn: 26.5960319	test: 26.5960319	test1: 27.5756577	best: 27.5756577 (300)	total: 181ms	remaining: 1.02s
350:	learn: 26.3110226	test: 26.3110226	test1: 27.3763728	best: 27.3763728 (350)	total: 207ms	remaining: 971ms
400:	learn: 26.0080594	test: 26.0080594	test1: 27.1651754

1it [00:01,  1.56s/it]


bestTest = 26.27882091
bestIteration = 1986

Shrink model to first 1987 iterations.
BEST ITERATION:  1986
mape на обучающей выборке: 0.213
mape на проверочной выборке: 0.246

********************** 1 фолд обучен! ******************************


==================== Обучение 2 фолда! ====================
0:	learn: 32.6588338	test: 32.6588338	test1: 29.5394690	best: 29.5394690 (0)	total: 1.19ms	remaining: 2.38s
50:	learn: 30.8164865	test: 30.8164865	test1: 27.9519094	best: 27.9519094 (50)	total: 31ms	remaining: 1.19s
100:	learn: 29.5498479	test: 29.5498479	test1: 26.9692189	best: 26.9692189 (100)	total: 57.3ms	remaining: 1.08s
150:	learn: 28.2567355	test: 28.2567355	test1: 25.9365558	best: 25.9365558 (150)	total: 90.4ms	remaining: 1.11s
200:	learn: 27.4833951	test: 27.4833951	test1: 25.3520357	best: 25.3520357 (200)	total: 120ms	remaining: 1.07s
250:	learn: 26.7830800	test: 26.7830800	test1: 24.8739298	best: 24.8739298 (250)	total: 150ms	remaining: 1.05s
300:	learn: 26.3047531	test: 26

2it [00:03,  1.52s/it]

mape на обучающей выборке: 0.208
mape на проверочной выборке: 0.214

********************** 2 фолд обучен! ******************************


==================== Обучение 3 фолда! ====================
0:	learn: 30.5453473	test: 30.5453473	test1: 34.1319560	best: 34.1319560 (0)	total: 897us	remaining: 1.79s
50:	learn: 28.9897023	test: 28.9897023	test1: 32.6976416	best: 32.6976416 (50)	total: 30.2ms	remaining: 1.15s
100:	learn: 27.9334515	test: 27.9334515	test1: 31.7929386	best: 31.7929386 (100)	total: 56.9ms	remaining: 1.07s
150:	learn: 27.2697711	test: 27.2697711	test1: 31.3201931	best: 31.3201931 (150)	total: 82.7ms	remaining: 1.01s
200:	learn: 26.5727734	test: 26.5727734	test1: 30.8134556	best: 30.8134556 (200)	total: 112ms	remaining: 1s
250:	learn: 25.9762769	test: 25.9762769	test1: 30.3923166	best: 30.3923166 (250)	total: 142ms	remaining: 990ms
300:	learn: 25.5306562	test: 25.5306562	test1: 30.0835466	best: 30.0835466 (300)	total: 167ms	remaining: 945ms
350:	learn: 25.1361516	test: 

3it [00:04,  1.50s/it]

1850:	learn: 22.3355857	test: 22.3355857	test1: 28.9680946	best: 28.9639254 (1825)	total: 1.06s	remaining: 85.2ms
1900:	learn: 22.3038962	test: 22.3038962	test1: 28.9685739	best: 28.9639254 (1825)	total: 1.09s	remaining: 56.8ms
1950:	learn: 22.2855474	test: 22.2855474	test1: 28.9691191	best: 28.9639254 (1825)	total: 1.12s	remaining: 28.2ms
1999:	learn: 22.2616636	test: 22.2616636	test1: 28.9688354	best: 28.9639254 (1825)	total: 1.15s	remaining: 0us

bestTest = 28.96392545
bestIteration = 1825

Shrink model to first 1826 iterations.
BEST ITERATION:  1825
mape на обучающей выборке: 0.201
mape на проверочной выборке: 0.253

********************** 3 фолд обучен! ******************************




In [51]:
catb_model_2.get_mean_cv_scores()

0.2375191336521265

In [52]:
catb_model_2._best_iters

[1986, 1974, 1825]

In [53]:
catb_model_2.get_extra_scores()

names               fold_1               fold_2               fold_3
0   mae_train            47,402.08            45,441.85            42,143.96
1   mae_valid            47,663.05            42,060.68            57,958.56
2   mse_train     5,980,256,505.25     5,419,725,951.91     4,677,322,372.51
3   mse_valid     4,969,483,139.91     4,489,964,802.78     8,469,666,377.31
4  rmse_train            77,332.12            73,618.79            68,390.95
5  rmse_valid            70,494.56            67,007.20            92,030.79

In [54]:
fi = catb_model_2.get_fi()
fi

index         importance_0         importance_1         importance_2  \
0     FullBath                19.58                16.83                26.56   
1  TotalBsmtSF                13.64                19.76                19.47   
2      LotArea                12.31                18.32                16.36   
3     PoolArea                17.67                 9.14                 1.81   
4   GarageQual                 9.27                 7.63                 7.64   
5   CentralAir                 6.22                 5.91                 9.34   
6  LotFrontage                 6.49                 8.61                 6.34   
7     SaleType                 7.37                 6.70                 4.56   
8     BldgType                 3.59                 4.30                 5.70   
9        Fence                 3.85                 2.80                 2.21   

       mean_importance  
0                20.99  
1                17.62  
2                15.66  
3                 9.54  
4                 8.18  
5                 7.15  
6                 7.15  
7                 6.21  
8                 4.53  
9                 2.95

In [55]:
catb_model_2.get_curve_plots()